In [1]:
import json
import pandas as pd
import numpy as np
import re
import networkx

In [2]:
!pip install konlpy

## 데이터 불러오기

In [3]:
def load_jsonl(path):
    data=[]
    with open(path, 'r', encoding='utf-8') as reader:
        for line in reader:
            data.append(json.loads(line))
    return data 

In [4]:
data_jsonl = load_jsonl("./추출요약/train.jsonl")
data_jsonl[0]

{'media': '당진시대',
 'id': '327827480',
 'article_original': ['당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.',
  '당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.',
  '이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며 “공연 자체를 무력화해 당진시를 망신 주려는 행위”라며 해당 문자를 보낸 단원 등 연루된 사람들을 찾아 사실관계를 확인하고 징계 등 책임을 물어야 한다고 지적했다.',
  '문제의 문자메세지를 전달받은 문화관광과는 감사법무담당관에게 조사를 의뢰했다.',
  '권경선 문화관광과장은 “누가, 어떻게 해서 해당 문자가 나온 것인지 정확히 조사해봐야 알 수 있다”며 “전달받은 문자 내용도 최 의원이 언급한 부분만 있어, 중간 내용만을 가지고는 전체를 유추할 수 없다”고 전했다.',
  '하지만 감사법무담당관실에서 아직 조사가 이뤄지지 않고 있어 당진시가 사태의 심각성을 인지하지 못하고 있다는 지적이다.',
  '그동안 행정사무감사가 진행되고 있어 사태를 지켜봤다던 감사법무담당관실에서는 “관계된 사람들을 조사해 사태를 파악해야 하는데, 아직 조사에 대한 뚜렷한 계획이 없다”고 답했다.',
  '한편 행감이 끝난 지난 12일 당진시의회에서는 당진시립합창단 문제를 비롯해 구체적인 조사가 필요한 부분에 대해 행정사무조사특별위원회를 구성해 운영하겠다고 밝혔다.',
  '김기재 의장은 “본회의 의결과 제적의원 1/3의 발의가 있으면 행정사무조사특별위원회를 구성할 수 있다”며 “다음 달 초 위원들과 상의해 위원회를 구성

In [5]:
df = pd.DataFrame(data_jsonl)
df.head()

media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   

                                         abstractive  extractive  
0  지난 6일 당진시의회 행정사무감사에서 '합창단이 소리를 작게 낼 것이니 알고 있으라...   [0, 1, 2]  
1  LA 에인절스의 최지만이 맹활약을 하여 시즌 타율 0.250에서 0.313으로 올리...   [0, 1, 3]  
2  16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가 ...  [6, 7, 10]  
3  대구·경북첨단의료산업진흥재단 의약생산센터는 약사법 시행규칙에서 정한 바에 따라 전용...   [1, 6, 4]  
4  식품의약품안전처는 29일 어린이가 즐겨마시는 음료를 대상으로 영양성분을 조사한 결과...  [2, 3, 10]

In [6]:
df['article_original'][2]

['인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아',
 '국유지로 임대료 없고 區서 지원도 일부 "사용 내역 공개 등 폐쇄적"',
 '인천시 부평구 산곡동 부영공원 야구장을 운영하는 구 생활체육야구협회를 두고 특혜 논란이 불거지고 있다.',
 '사진은 부영공원 야구장 전경.',
 '김유리 기자 kyr@kihoilbo.co.kr',
 '인천시 부평구생활체육야구협회가 깜깜이로 부영공원을 운영하고 있다는 지적이 나오고 있다.',
 '16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가 무상 사용하면서 이곳을 이용하는 야구동호회(80여 개 팀)로부터 팀별로 연간 260만 원씩 회비를 받고 있다.',
 '문제는 회비 산정 기준과 사용 내역이 투명하게 공개되지 않고 있다는 것이다.',
 '회비는 협회에서 주관하는 사회인 야구리그 운영 및 구장 관리에 사용된다.',
 '경기마다 심판 2명과 점수 기록원의 인건비 각 5만 원, 야구공 구입비, 구장 청소 비용 등으로 약 20만 원의 비용이 발생한다.',
 '일부 리그 회원들은 예결산 내역을 각 야구팀 감독들에게만 공개하는 등 폐쇄적으로 운영되고 있다고 지적했다.',
 '게다가 현금 사용이 많고 영수증 등 증빙자료가 없는 경우도 있어 신뢰하기 어렵다며 의혹을 제기했다.',
 '또 국유지를 임대료 없이 무상 사용하고 있고, 마사토 구입 등은 구 예산을 지원받는 협회가 회비까지 걷는 것은 지나친 특혜라는 주장이다.',
 '이들은 구가 직접 관리 주체가 되거나 공모 등을 통해 위탁운영을 정식으로 맡기기를 요구하고 있다.',
 '상황이 이런데도 구는 생활체육회에 관리·감독 권한을 행사할 수 없다는 이유로 방관하고 있다.',
 '현재 구생활체육회의 관리 권한은 인천시생활체육회가 갖고 있는데다, 민간단체이기 때문에 사용 내역을 요구할 수 없다는 것이다.',
 '부평구생활체육협회 리그에 소속된 야구팀에서 활동하고 있는 A(46)씨는 "협회가 국유지를 공짜로 사용하면서 수익활동을 하고 있

## 전처리 & EDA

In [7]:
len(df)

42803

In [8]:
df.isnull().sum()

media               0
id                  0
article_original    0
abstractive         0
extractive          0
dtype: int64

#### 'extractive' 칼럼의 인덱스를 문장으로 바꿔서 'ex_sent'칼럼 만들기

In [9]:
type(df['extractive'][0][1])

int

In [10]:
df['ex_sent'] ='a'

for i in range(len(df)):
    ex_sent = []
    for j in range(len(df['extractive'][i])):
        idx = df['extractive'][i][j]
        ex_sent.append(df['article_original'][i][idx])
    df['ex_sent'][i] = ex_sent
        
df['ex_sent'][2]

['16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가 무상 사용하면서 이곳을 이용하는 야구동호회(80여 개 팀)로부터 팀별로 연간 260만 원씩 회비를 받고 있다.',
 '문제는 회비 산정 기준과 사용 내역이 투명하게 공개되지 않고 있다는 것이다.',
 '일부 리그 회원들은 예결산 내역을 각 야구팀 감독들에게만 공개하는 등 폐쇄적으로 운영되고 있다고 지적했다.']

In [11]:
df.head()

media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   

                                         abstractive  extractive  \
0  지난 6일 당진시의회 행정사무감사에서 '합창단이 소리를 작게 낼 것이니 알고 있으라...   [0, 1, 2]   
1  LA 에인절스의 최지만이 맹활약을 하여 시즌 타율 0.250에서 0.313으로 올리...   [0, 1, 3]   
2  16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가 ...  [6, 7, 10]   
3  대구·경북첨단의료산업진흥재단 의약생산센터는 약사법 시행규칙에서 정한 바에 따라 전용...   [1, 6, 4]   
4  식품의약품안전처는 29일 어린이가 즐겨마시는 음료를 대상으로 영양성분을 조사한 결과...  [2, 3, 10]   

                                             ex_sent  
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...  
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...  
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...  
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...  
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...

In [12]:
data = df[['media','id','article_original','ex_sent']]
data.head()

media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   

                                             ex_sent  
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...  
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...  
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...  
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...  
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...

#### 명사 뽑기 - Okt

In [13]:
from konlpy.tag import Okt

def okt(textlist):

        okt = Okt()
        nounlist = []
        
        for i in range(len(textlist)):
            n = re.sub('[-=.#/:$}·,■?]','',str(textlist[i]))
            k = re.sub('[0-9]','',n)
            nounlist.append(okt.nouns(k))


        return nounlist

In [14]:
okt_result = okt(data['article_original'][0])
okt_result

[['당진시',
  '문화',
  '관광',
  '대상',
  '행정',
  '사무',
  '감사',
  '당진',
  '시립',
  '합창단',
  '관계자',
  '것',
  '추정',
  '문자',
  '관련',
  '당진시',
  '의회',
  '행정사',
  '무조',
  '특별',
  '위원회',
  '구성',
  '조사'],
 ['당진시',
  '의회',
  '행정',
  '사무',
  '감사',
  '일차',
  '지난',
  '일',
  '문화',
  '관광',
  '대상',
  '행감',
  '최창용',
  '의원',
  '당진',
  '시립',
  '합창단',
  '정기',
  '연주회',
  '문자',
  '메세지',
  '제보',
  '며',
  '음향',
  '팀',
  '것',
  '추정',
  '해당',
  '문자',
  '합창단',
  '소리',
  '낼',
  '것',
  '알',
  '내용',
  '고',
  '말'],
 ['공연',
  '소리',
  '것',
  '합창단',
  '그',
  '임무',
  '것',
  '공연',
  '자체',
  '무력',
  '화해',
  '당진시',
  '망신',
  '행위',
  '라며',
  '해당',
  '문자',
  '단원',
  '등',
  '연루',
  '사람',
  '사실관계',
  '확인',
  '징계',
  '등',
  '책임',
  '물어',
  '지적'],
 ['문제', '문자', '메세지', '전달', '문화', '관광', '감사', '법무', '담당', '관', '조사', '의뢰'],
 ['권',
  '경선',
  '문화',
  '관광',
  '과장',
  '누가',
  '해당',
  '문자',
  '것',
  '조사',
  '알',
  '수',
  '며',
  '전달',
  '문자',
  '내용',
  '최',
  '의원',
  '언급',
  '부분',
  '중간',
  '내용',
  '전체',
  '유추',
  '수',
  '고',
  '전'],
 ['감사', '

In [15]:
flat=[]
for i in okt_result:
    for j in i:
        flat.append(j)

In [16]:
from collections import Counter
Counter(flat).most_common() 

[('문자', 7),
 ('당진시', 6),
 ('감사', 6),
 ('합창단', 6),
 ('것', 6),
 ('조사', 6),
 ('문화', 4),
 ('관광', 4),
 ('당진', 4),
 ('시립', 4),
 ('위원회', 4),
 ('구성', 4),
 ('행정', 3),
 ('사무', 3),
 ('의회', 3),
 ('행정사', 3),
 ('무조', 3),
 ('특별', 3),
 ('의원', 3),
 ('며', 3),
 ('해당', 3),
 ('내용', 3),
 ('고', 3),
 ('등', 3),
 ('법무', 3),
 ('담당', 3),
 ('수', 3),
 ('사태', 3),
 ('대상', 2),
 ('추정', 2),
 ('관련', 2),
 ('지난', 2),
 ('일', 2),
 ('행감', 2),
 ('메세지', 2),
 ('소리', 2),
 ('알', 2),
 ('말', 2),
 ('공연', 2),
 ('사람', 2),
 ('지적', 2),
 ('문제', 2),
 ('전달', 2),
 ('부분', 2),
 ('관실', 2),
 ('계획', 2),
 ('비롯', 2),
 ('대해', 2),
 ('관계자', 1),
 ('일차', 1),
 ('최창용', 1),
 ('정기', 1),
 ('연주회', 1),
 ('제보', 1),
 ('음향', 1),
 ('팀', 1),
 ('낼', 1),
 ('그', 1),
 ('임무', 1),
 ('자체', 1),
 ('무력', 1),
 ('화해', 1),
 ('망신', 1),
 ('행위', 1),
 ('라며', 1),
 ('단원', 1),
 ('연루', 1),
 ('사실관계', 1),
 ('확인', 1),
 ('징계', 1),
 ('책임', 1),
 ('물어', 1),
 ('관', 1),
 ('의뢰', 1),
 ('권', 1),
 ('경선', 1),
 ('과장', 1),
 ('누가', 1),
 ('최', 1),
 ('언급', 1),
 ('중간', 1),
 ('전체', 1),
 ('유추', 1),
 ('전', 1

In [17]:
data['ex_sent'][0]

['당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.',
 '당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.',
 '이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며 “공연 자체를 무력화해 당진시를 망신 주려는 행위”라며 해당 문자를 보낸 단원 등 연루된 사람들을 찾아 사실관계를 확인하고 징계 등 책임을 물어야 한다고 지적했다.']

## TextRank - 0번 행으로 테스트

* TextRank 를 이용한 키워드 추출과 핵심 문장 추출 (구현과 실험) https://lovit.github.io/nlp/2019/04/30/textrank/
* 깃헙 https://github.com/lovit/textrank/
* KR-WordRank 를 이용한 핵심 문장 추출과 ROUGE 를 이용한 요약문 성능 평가 https://lovit.github.io/nlp/2019/05/01/krwordrank_sentence/
* Unsupervised tokenizers in soynlp project https://lovit.github.io/nlp/2018/04/09/three_tokenizers_soynlp/


In [18]:
!pip install git+https://github.com/lovit/textrank.git

  Cloning https://github.com/lovit/textrank.git to /private/var/folders/4c/mzcsk3jd4bx053t6khbcnjj80000gn/T/pip-req-build-3hy2zwl9
  Created wheel for textrank: filename=textrank-0.1.2-py3-none-any.whl size=11170 sha256=a9a884005b5231f2232b3d14d828fc32e2454484b6778d8d98b09ec479aefc9e
  Stored in directory: /private/var/folders/4c/mzcsk3jd4bx053t6khbcnjj80000gn/T/pip-ephem-wheel-cache-2b51svjq/wheels/88/fe/9c/129f61ac6c8c9b04f4d33fc3a39560cb97997b1b59c064ffd3
Successfully built textrank


In [19]:
from konlpy.tag import Komoran
import textrank

komoran = Komoran()


# 명사, 동사, 형용사, 어간의 품사만 뽑는 함수

def komoran_tokenize(sent):
    words = komoran.pos(sent, join=True)
    words = [w for w in words if ('/NN' in w or '/XR' in w or '/VA' in w or '/VV' in w)]
    return words

In [20]:
# 0번 행을 데이터(sents)로 지정

sents = data['article_original'][0]
sents

['당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.',
 '당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.',
 '이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며 “공연 자체를 무력화해 당진시를 망신 주려는 행위”라며 해당 문자를 보낸 단원 등 연루된 사람들을 찾아 사실관계를 확인하고 징계 등 책임을 물어야 한다고 지적했다.',
 '문제의 문자메세지를 전달받은 문화관광과는 감사법무담당관에게 조사를 의뢰했다.',
 '권경선 문화관광과장은 “누가, 어떻게 해서 해당 문자가 나온 것인지 정확히 조사해봐야 알 수 있다”며 “전달받은 문자 내용도 최 의원이 언급한 부분만 있어, 중간 내용만을 가지고는 전체를 유추할 수 없다”고 전했다.',
 '하지만 감사법무담당관실에서 아직 조사가 이뤄지지 않고 있어 당진시가 사태의 심각성을 인지하지 못하고 있다는 지적이다.',
 '그동안 행정사무감사가 진행되고 있어 사태를 지켜봤다던 감사법무담당관실에서는 “관계된 사람들을 조사해 사태를 파악해야 하는데, 아직 조사에 대한 뚜렷한 계획이 없다”고 답했다.',
 '한편 행감이 끝난 지난 12일 당진시의회에서는 당진시립합창단 문제를 비롯해 구체적인 조사가 필요한 부분에 대해 행정사무조사특별위원회를 구성해 운영하겠다고 밝혔다.',
 '김기재 의장은 “본회의 의결과 제적의원 1/3의 발의가 있으면 행정사무조사특별위원회를 구성할 수 있다”며 “다음 달 초 위원들과 상의해 위원회를 구성한다면 당진시립합창단 관련 사안을 비롯해 사회복지기관 위수탁 등에 대해 다룰 계획”이라고 말했다.']

#### 핵심 단어 선정

In [21]:
from textrank import KeywordSummarizer

keyword_extractor = KeywordSummarizer(
    tokenize = komoran_tokenize,
    window = -1,
    verbose = False
)

keywords = keyword_extractor.summarize(sents, topk=30)
for word, rank in keywords:
    print('{} ({:.3})'.format(word, rank))

당진시/NNP (2.93)
조사/NNG (2.37)
합창단/NNG (1.97)
것/NNB (1.95)
문자/NNG (1.87)
행정사/NNP (1.83)
하/VV (1.75)
감사/NNP (1.53)
있/VV (1.49)
립/NNG (1.33)
관광/NNP (1.23)
문화/NNG (1.23)
위원회/NNG (1.15)
구성/NNG (1.15)
의회/NNP (1.1)
보내/VV (1.08)
내용/NNG (1.03)
해당/NNG (1.02)
받/VV (0.933)
특별/NNG (0.914)
추정/NNG (0.853)
대상/NNG (0.853)
과/NNG (0.853)
수/NNB (0.85)
대하/VV (0.828)
등/NNB (0.823)
지나/VV (0.803)
일/NNB (0.803)
행/NNG (0.803)
감/NNG (0.803)


#### 핵심 문장 선택

In [22]:
from textrank import KeysentenceSummarizer

summarizer = KeysentenceSummarizer(
    tokenize = komoran_tokenize,
    min_sim = 0.5,
    verbose = True
)
keysents = summarizer.summarize(sents)
for idx, rank, komoran_sent in keysents:
    print('#{} ({:.3}) : {}'.format(idx, rank, sents[idx]), end='\n\n')

calculating textrank sentence similarity was done with 9 sents
trained TextRank. n sentences = 9
#1 (1.49) : 당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.

#0 (1.34) : 당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.

#8 (1.06) : 김기재 의장은 “본회의 의결과 제적의원 1/3의 발의가 있으면 행정사무조사특별위원회를 구성할 수 있다”며 “다음 달 초 위원들과 상의해 위원회를 구성한다면 당진시립합창단 관련 사안을 비롯해 사회복지기관 위수탁 등에 대해 다룰 계획”이라고 말했다.

#4 (0.981) : 권경선 문화관광과장은 “누가, 어떻게 해서 해당 문자가 나온 것인지 정확히 조사해봐야 알 수 있다”며 “전달받은 문자 내용도 최 의원이 언급한 부분만 있어, 중간 내용만을 가지고는 전체를 유추할 수 없다”고 전했다.

#6 (0.924) : 그동안 행정사무감사가 진행되고 있어 사태를 지켜봤다던 감사법무담당관실에서는 “관계된 사람들을 조사해 사태를 파악해야 하는데, 아직 조사에 대한 뚜렷한 계획이 없다”고 답했다.

#7 (0.912) : 한편 행감이 끝난 지난 12일 당진시의회에서는 당진시립합창단 문제를 비롯해 구체적인 조사가 필요한 부분에 대해 행정사무조사특별위원회를 구성해 운영하겠다고 밝혔다.

#3 (0.828) : 문제의 문자메세지를 전달받은 문화관광과는 감사법무담당관에게 조사를 의뢰했다.

#2 (0.737) : 이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며

In [23]:
# 확인

data['ex_sent'][0]

['당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.',
 '당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.',
 '이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며 “공연 자체를 무력화해 당진시를 망신 주려는 행위”라며 해당 문자를 보낸 단원 등 연루된 사람들을 찾아 사실관계를 확인하고 징계 등 책임을 물어야 한다고 지적했다.']

**=> 두 문장 맞음!**

## TextRank - lovit ver.


In [24]:
from konlpy.tag import Komoran
import textrank
from textrank import KeywordSummarizer
from textrank import KeysentenceSummarizer
import tqdm

#### 전처리 + 토큰화

In [25]:
komoran = Komoran()

# kmomoran 토큰화 함수 
def tokenize_komoran(textlist):
    nounlist = []
    for i in range(len(textlist)):
        n = re.sub('[-=.#/:$}·,■?]','',str(textlist[i]))
        k = re.sub('[0-9]','',n)
        nounlist.append(komoran.nouns(k))
    return nounlist
            

# 명사, 동사, 형용사, 어간만 뽑는 함수
def komoran_tokenize(sent):
    words = komoran.pos(sent, join=True)
    words = [w for w in words if ('/NN' in w or '/XR' in w or '/VA' in w or '/VV' in w)]
    return words


# 리스트를 1차원으로 flatten 시키는 함수
def make_flat(list_):
    flat=[]
    for i in list_:
        for j in i:
            flat.append(j)
    return flat


# 불용어, stopwords, 한글자 제거하는 함수
def remove_token(text): 
    stopwords = []
    text = [word for word in text if word not in stopwords]
    text = [word for word in text if len(word)!=1]
    return text


In [44]:
dt = data[:10]
dt

media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   
5  국제신문  335954082  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  당진시대  328783742  [내년 1월부터 당진시가 삽교호 수질오염 총량관리제를 실시한다., 본격적인 제도 시...   
7  경기일보  330375647  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  기호일보  359531654  [▲ 전국요양서비스노동조합 경기지부는 10일 오전 경기도청 정문 앞에서 사회서비스원...   
9  대전일보  337356183  [옥천군 다람쥐택시 이용 모습., 사진=옥천군 제공, [옥천]옥천 오지마을 주민들의...   

                                             ex_sent  
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...  
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...  
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...  
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...  
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...  
5  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...  
6  [본격적인 제도 시행을 앞두고 당진시는 지난 19일 삽교호 수질오염총량관리 시행계획...  
7  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...  
8  [민주노총 서비스연맹 전국요양서비스노동조합 경기지부는 10일 경기도청 정문 앞에서 ...  
9  [옥천군은 기존 20개 마을에서 운영해 왔던 다람쥐택시를 올해부터 24개 마을로 확...

In [27]:
# 토큰화
dt['token'] = dt['article_original'].map(tokenize_komoran)
dt

<ipython-input-27-215b0adf8742>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dt['token'] = dt['article_original'].map(tokenize_komoran)


media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   
5  국제신문  335954082  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  당진시대  328783742  [내년 1월부터 당진시가 삽교호 수질오염 총량관리제를 실시한다., 본격적인 제도 시...   
7  경기일보  330375647  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  기호일보  359531654  [▲ 전국요양서비스노동조합 경기지부는 10일 오전 경기도청 정문 앞에서 사회서비스원...   
9  대전일보  337356183  [옥천군 다람쥐택시 이용 모습., 사진=옥천군 제공, [옥천]옥천 오지마을 주민들의...   

                                             ex_sent  \
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...   
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...   
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...   
5  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  [본격적인 제도 시행을 앞두고 당진시는 지난 19일 삽교호 수질오염총량관리 시행계획...   
7  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  [민주노총 서비스연맹 전국요양서비스노동조합 경기지부는 10일 경기도청 정문 앞에서 ...   
9  [옥천군은 기존 20개 마을에서 운영해 왔던 다람쥐택시를 올해부터 24개 마을로 확...   

                                               token  
0  [[당진시, 문화, 관광, 과, 대상, 행정사, 감사, 당진시, 립, 합창단, 관계...  
1  [[미국, 메이저, 리그, 활동, 한국, 선수, 시즌, 초반, 희비], [에인절스,...  
2  [[인천, 부영공원, 운영, 생활, 야구, 협회, 여, 동호회, 팀, 원], [국유...  
3  [[대구경북첨단의료산업진흥재단, 의약, 생산, 센터, 항암, 주사제, 균, 충전, ...  
4  [[국내, 유통, 탄산, 음료, 중, 식품, 의약품, 안전, 처, 품질, 인증, 제...  
5  [[북한, 베트남, 하노이, 차, 북미, 정상회담, 합의문, 서명, 결렬, 사실, ...  
6  [[내년, 월, 당진시, 삽교호, 수질, 오염, 총량, 관리제, 실시], [제도, ...  
7  [[지방, 선거, 허위, 사실, 유포, 혐의, 기소, 안, 승, 남, 구리시, 장,...  
8  [[전국, 요양, 서비스, 노동조합, 경기, 지부, 일, 오전, 경기도청, 정문, ...  
9  [[옥천군, 다람쥐, 택시, 이용, 모습], [사진, 옥천군, 제공], [옥천, 옥...

In [28]:
# 1차원 리스트로 변환
dt['token_flat'] = dt['token'].map(make_flat)
dt

<ipython-input-28-05c9d69a3c92>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dt['token_flat'] = dt['token'].map(make_flat)


media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   
5  국제신문  335954082  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  당진시대  328783742  [내년 1월부터 당진시가 삽교호 수질오염 총량관리제를 실시한다., 본격적인 제도 시...   
7  경기일보  330375647  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  기호일보  359531654  [▲ 전국요양서비스노동조합 경기지부는 10일 오전 경기도청 정문 앞에서 사회서비스원...   
9  대전일보  337356183  [옥천군 다람쥐택시 이용 모습., 사진=옥천군 제공, [옥천]옥천 오지마을 주민들의...   

                                             ex_sent  \
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...   
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...   
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...   
5  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  [본격적인 제도 시행을 앞두고 당진시는 지난 19일 삽교호 수질오염총량관리 시행계획...   
7  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  [민주노총 서비스연맹 전국요양서비스노동조합 경기지부는 10일 경기도청 정문 앞에서 ...   
9  [옥천군은 기존 20개 마을에서 운영해 왔던 다람쥐택시를 올해부터 24개 마을로 확...   

                                               token  \
0  [[당진시, 문화, 관광, 과, 대상, 행정사, 감사, 당진시, 립, 합창단, 관계...   
1  [[미국, 메이저, 리그, 활동, 한국, 선수, 시즌, 초반, 희비], [에인절스,...   
2  [[인천, 부영공원, 운영, 생활, 야구, 협회, 여, 동호회, 팀, 원], [국유...   
3  [[대구경북첨단의료산업진흥재단, 의약, 생산, 센터, 항암, 주사제, 균, 충전, ...   
4  [[국내, 유통, 탄산, 음료, 중, 식품, 의약품, 안전, 처, 품질, 인증, 제...   
5  [[북한, 베트남, 하노이, 차, 북미, 정상회담, 합의문, 서명, 결렬, 사실, ...   
6  [[내년, 월, 당진시, 삽교호, 수질, 오염, 총량, 관리제, 실시], [제도, ...   
7  [[지방, 선거, 허위, 사실, 유포, 혐의, 기소, 안, 승, 남, 구리시, 장,...   
8  [[전국, 요양, 서비스, 노동조합, 경기, 지부, 일, 오전, 경기도청, 정문, ...   
9  [[옥천군, 다람쥐, 택시, 이용, 모습], [사진, 옥천군, 제공], [옥천, 옥...   

                                          token_flat  
0  [당진시, 문화, 관광, 과, 대상, 행정사, 감사, 당진시, 립, 합창단, 관계자...  
1  [미국, 메이저, 리그, 활동, 한국, 선수, 시즌, 초반, 희비, 에인절스, 최지...  
2  [인천, 부영공원, 운영, 생활, 야구, 협회, 여, 동호회, 팀, 원, 국유지, ...  
3  [대구경북첨단의료산업진흥재단, 의약, 생산, 센터, 항암, 주사제, 균, 충전, 시...  
4  [국내, 유통, 탄산, 음료, 중, 식품, 의약품, 안전, 처, 품질, 인증, 제품...  
5  [북한, 베트남, 하노이, 차, 북미, 정상회담, 합의문, 서명, 결렬, 사실, 언...  
6  [내년, 월, 당진시, 삽교호, 수질, 오염, 총량, 관리제, 실시, 제도, 시행,...  
7  [지방, 선거, 허위, 사실, 유포, 혐의, 기소, 안, 승, 남, 구리시, 장, ...  
8  [전국, 요양, 서비스, 노동조합, 경기, 지부, 일, 오전, 경기도청, 정문, 앞...  
9  [옥천군, 다람쥐, 택시, 이용, 모습, 사진, 옥천군, 제공, 옥천, 옥천, 오지...

In [29]:
# 불용어, stopword, 한글자 제거
dt['token_flat'] = dt['token_flat'].map(remove_token)
dt

<ipython-input-29-36939028e7ce>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dt['token_flat'] = dt['token_flat'].map(remove_token)


media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   
5  국제신문  335954082  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  당진시대  328783742  [내년 1월부터 당진시가 삽교호 수질오염 총량관리제를 실시한다., 본격적인 제도 시...   
7  경기일보  330375647  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  기호일보  359531654  [▲ 전국요양서비스노동조합 경기지부는 10일 오전 경기도청 정문 앞에서 사회서비스원...   
9  대전일보  337356183  [옥천군 다람쥐택시 이용 모습., 사진=옥천군 제공, [옥천]옥천 오지마을 주민들의...   

                                             ex_sent  \
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...   
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...   
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...   
5  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  [본격적인 제도 시행을 앞두고 당진시는 지난 19일 삽교호 수질오염총량관리 시행계획...   
7  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  [민주노총 서비스연맹 전국요양서비스노동조합 경기지부는 10일 경기도청 정문 앞에서 ...   
9  [옥천군은 기존 20개 마을에서 운영해 왔던 다람쥐택시를 올해부터 24개 마을로 확...   

                                               token  \
0  [[당진시, 문화, 관광, 과, 대상, 행정사, 감사, 당진시, 립, 합창단, 관계...   
1  [[미국, 메이저, 리그, 활동, 한국, 선수, 시즌, 초반, 희비], [에인절스,...   
2  [[인천, 부영공원, 운영, 생활, 야구, 협회, 여, 동호회, 팀, 원], [국유...   
3  [[대구경북첨단의료산업진흥재단, 의약, 생산, 센터, 항암, 주사제, 균, 충전, ...   
4  [[국내, 유통, 탄산, 음료, 중, 식품, 의약품, 안전, 처, 품질, 인증, 제...   
5  [[북한, 베트남, 하노이, 차, 북미, 정상회담, 합의문, 서명, 결렬, 사실, ...   
6  [[내년, 월, 당진시, 삽교호, 수질, 오염, 총량, 관리제, 실시], [제도, ...   
7  [[지방, 선거, 허위, 사실, 유포, 혐의, 기소, 안, 승, 남, 구리시, 장,...   
8  [[전국, 요양, 서비스, 노동조합, 경기, 지부, 일, 오전, 경기도청, 정문, ...   
9  [[옥천군, 다람쥐, 택시, 이용, 모습], [사진, 옥천군, 제공], [옥천, 옥...   

                                          token_flat  
0  [당진시, 문화, 관광, 대상, 행정사, 감사, 당진시, 합창단, 관계자, 추정, ...  
1  [미국, 메이저, 리그, 활동, 한국, 선수, 시즌, 초반, 희비, 에인절스, 최지...  
2  [인천, 부영공원, 운영, 생활, 야구, 협회, 동호회, 국유지, 임대료, 지원, ...  
3  [대구경북첨단의료산업진흥재단, 의약, 생산, 센터, 항암, 주사제, 충전, 시설, ...  
4  [국내, 유통, 탄산, 음료, 식품, 의약품, 안전, 품질, 인증, 제품, 혼합, ...  
5  [북한, 베트남, 하노이, 북미, 정상회담, 합의문, 서명, 결렬, 사실, 언급, ...  
6  [내년, 당진시, 삽교호, 수질, 오염, 총량, 관리제, 실시, 제도, 시행, 당진...  
7  [지방, 선거, 허위, 사실, 유포, 혐의, 기소, 구리시, 재판, 혐의, 부인, ...  
8  [전국, 요양, 서비스, 노동조합, 경기, 지부, 오전, 경기도청, 정문, 사회, ...  
9  [옥천군, 다람쥐, 택시, 이용, 모습, 사진, 옥천군, 제공, 옥천, 옥천, 오지...

#### 핵심 단어 확인

In [30]:
from textrank import KeywordSummarizer

keyword_extractor = KeywordSummarizer(
    tokenize = komoran_tokenize,
    window = -1,
    verbose = False
)

# 토큰화 한 버전
keywords = keyword_extractor.summarize(dt['token_flat'][0], topk=10)
for word, rank in keywords:
    print('{} ({:.3})'.format(word, rank))

print("-------------------")


# 토큰화 안 한 버전
keywords = keyword_extractor.summarize(data['article_original'][0], topk=10)
for word, rank in keywords:
    print('{} ({:.3})'.format(word, rank))

계획/NNG (0.15)
법무/NNP (0.15)
조사/NNG (0.15)
문자/NNP (0.15)
행정사/NNP (0.15)
감사/NNG (0.15)
합창단/NNG (0.15)
문화/NNG (0.15)
관광/NNP (0.15)
위원회/NNG (0.15)
-------------------
당진시/NNP (2.93)
조사/NNG (2.37)
합창단/NNG (1.97)
것/NNB (1.95)
문자/NNG (1.87)
행정사/NNP (1.83)
하/VV (1.75)
감사/NNP (1.53)
있/VV (1.49)
립/NNG (1.33)


In [54]:
dt['token_pos'] = ''
def komoran_tokenize(sent):
    words = komoran.pos(sent, join=True)
    words = [w for w in words if ('/NN' in w or '/XR' in w or '/VA' in w or '/VV' in w)]
    return words

for i in range(len(dt)):
    dt['token_pos'][i] = []
    for j in range(len(dt['article_original'][i])):
        dt['token_pos'][i].append(komoran_tokenize(dt['article_original'][i][j]))
        
dt['token_pos'][0]
    

<ipython-input-54-849a1e700961>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dt['token_pos'] = ''


[['당진시/NNP',
  '문화/NNG',
  '관광/NNP',
  '과/NNG',
  '대상/NNG',
  '하/VV',
  '행정사/NNP',
  '감사/NNP',
  '당진시/NNP',
  '립/NNG',
  '합창단/NNG',
  '관계자/NNG',
  '보내/VV',
  '것/NNB',
  '추정/NNG',
  '문자/NNG',
  '관련/NNG',
  '당진시/NNP',
  '의회/NNP',
  '행정사/NNP',
  '조사/NNG',
  '특별/NNG',
  '위원회/NNG',
  '구성/NNG',
  '조사/NNG',
  '밝히/VV'],
 ['당진시/NNP',
  '의회/NNP',
  '행정사/NNP',
  '감사/NNP',
  '일차/NNG',
  '지나/VV',
  '일/NNB',
  '문화/NNG',
  '관광/NNP',
  '과/NNG',
  '대상/NNG',
  '하/VV',
  '행/NNG',
  '감/NNG',
  '창/NNG',
  '의원/NNG',
  '당진시/NNP',
  '립/NNG',
  '합창단/NNG',
  '정기/NNP',
  '연주회/NNP',
  '앞두/VV',
  '문자/NNG',
  '메세지/NNG',
  '제보/NNG',
  '받/VV',
  '음향/NNG',
  '팀/NNG',
  '보내/VV',
  '것/NNB',
  '추정/NNG',
  '해당/NNG',
  '문자/NNG',
  '합창단/NNG',
  '소리/NNG',
  '작/VA',
  '내/VV',
  '것/NNB',
  '알/VV',
  '있/VV',
  '내용/NNG',
  '말/NNG'],
 ['공연/NNP',
  '소리/NNG',
  '작/VA',
  '내/VV',
  '것/NNB',
  '합창단/NNG',
  '임무/NNG',
  '하/VV',
  '것/NNB',
  '공연/NNP',
  '자체/NNG',
  '무력/NNG',
  '화해/NNP',
  '당진시/NNP',
  '망신/NNG',
  '행위/NNG',
  '해당/NNG',
 

In [57]:
def pos_to_string(list_):
    
    i_list=[]
    
    for i in range(len(list_)):
        
        j_str = ''
        
        for j in range(len(list_[i])):
            
            j_str = j_str + str(list_[i][j]) + ' '
        
        i_list.append(j_str)
    
    return i_list

In [60]:
dt['token_str'] = dt['token_pos'].map(pos_to_string)
dt['token_str'][0]

<ipython-input-60-bf7a4844d741>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dt['token_str'] = dt['token_pos'].map(pos_to_string)


['당진시/NNP 문화/NNG 관광/NNP 과/NNG 대상/NNG 하/VV 행정사/NNP 감사/NNP 당진시/NNP 립/NNG 합창단/NNG 관계자/NNG 보내/VV 것/NNB 추정/NNG 문자/NNG 관련/NNG 당진시/NNP 의회/NNP 행정사/NNP 조사/NNG 특별/NNG 위원회/NNG 구성/NNG 조사/NNG 밝히/VV ',
 '당진시/NNP 의회/NNP 행정사/NNP 감사/NNP 일차/NNG 지나/VV 일/NNB 문화/NNG 관광/NNP 과/NNG 대상/NNG 하/VV 행/NNG 감/NNG 창/NNG 의원/NNG 당진시/NNP 립/NNG 합창단/NNG 정기/NNP 연주회/NNP 앞두/VV 문자/NNG 메세지/NNG 제보/NNG 받/VV 음향/NNG 팀/NNG 보내/VV 것/NNB 추정/NNG 해당/NNG 문자/NNG 합창단/NNG 소리/NNG 작/VA 내/VV 것/NNB 알/VV 있/VV 내용/NNG 말/NNG ',
 '공연/NNP 소리/NNG 작/VA 내/VV 것/NNB 합창단/NNG 임무/NNG 하/VV 것/NNB 공연/NNP 자체/NNG 무력/NNG 화해/NNP 당진시/NNP 망신/NNG 행위/NNG 해당/NNG 문자/NNG 보내/VV 단원/NNG 등/NNB 연루/NNG 사람/NNG 찾/VV 사실관계/NNP 확인/NNG 징계/NNG 등/NNB 책임/NNG 묻/VV 하/VV 지적/NNG ',
 '문제/NNG 문자/NNG 메세지/NNG 전달/NNG 받/VV 문화/NNG 관광/NNP 감사/NNP 법무/NNP 담당관/NNG 조사/NNG 의뢰/NNG ',
 '권/NNB 경선/NNP 문화/NNG 관광/NNP 과장/NNG 누가/NNP 어떻/VA 하/VV 해당/NNG 문자/NNG 나오/VV 것/NNB 조사/NNG 알/VV 수/NNB 있다/NNP 전달/NNG 받/VV 문자/NNP 내용/NNG 최/NNP 의원/NNG 언급/NNG 부분/NNG 있/VV 중간/NNG 내용/NNG 가지/VV 전체/NNG 유추/NNG 수/NNB 없/VA 전하/VV ',
 '감사/NNP 

In [61]:
dt

media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   
5  국제신문  335954082  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  당진시대  328783742  [내년 1월부터 당진시가 삽교호 수질오염 총량관리제를 실시한다., 본격적인 제도 시...   
7  경기일보  330375647  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  기호일보  359531654  [▲ 전국요양서비스노동조합 경기지부는 10일 오전 경기도청 정문 앞에서 사회서비스원...   
9  대전일보  337356183  [옥천군 다람쥐택시 이용 모습., 사진=옥천군 제공, [옥천]옥천 오지마을 주민들의...   

                                             ex_sent  \
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...   
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...   
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...   
5  [북한은 베트남 하노이에서 열린 제2차 북미 정상회담에서 합의문에 서명도 하지 못하...   
6  [본격적인 제도 시행을 앞두고 당진시는 지난 19일 삽교호 수질오염총량관리 시행계획...   
7  [6·13 지방선거에 앞서 허위사실을 유포한 혐의로 기소된 안승남 구리시장(54)이...   
8  [민주노총 서비스연맹 전국요양서비스노동조합 경기지부는 10일 경기도청 정문 앞에서 ...   
9  [옥천군은 기존 20개 마을에서 운영해 왔던 다람쥐택시를 올해부터 24개 마을로 확...   

                                           token_pos  \
0  [[당진시/NNP, 문화/NNG, 관광/NNP, 과/NNG, 대상/NNG, 하/VV...   
1  [[미국/NNP, 메이저/NNP, 리그/NNP, 활동/NNG, 한국/NNP, 선수/...   
2  [[인천/NNP, 부영공원/NNP, 운영/NNG, 생활/NNG, 야구/NNP, 협회...   
3  [[대구/NNP, 경북/NNP, 첨단/NNG, 의료/NNP, 산업/NNP, 진흥/N...   
4  [[국내/NNG, 유통/NNG, 탄산/NNP, 음료/NNP, 중/NNB, 식품/NN...   
5  [[북한/NNP, 베트남/NNP, 하노이/NNP, 열리/VV, 차/NNB, 북미/N...   
6  [[내년/NNG, 1월/NNP, 당진시/NNP, 삽교호/NNP, 수질/NNP, 오염...   
7  [[지방/NNG, 선거/NNG, 허위/NNP, 사실/NNG, 유포/NNG, 혐의/N...   
8  [[전국/NNP, 요양/NNP, 서비스/NNP, 노동조합/NNP, 경기/NNG, 지...   
9  [[옥천군/NNP, 다람쥐/NNP, 택시/NNP, 이용/NNG, 모습/NNG], [...   

                                           token_str  
0  [당진시/NNP 문화/NNG 관광/NNP 과/NNG 대상/NNG 하/VV 행정사/N...  
1  [미국/NNP 메이저/NNP 리그/NNP 활동/NNG 한국/NNP 선수/NNG 시즌...  
2  [인천/NNP 부영공원/NNP 운영/NNG 생활/NNG 야구/NNP 협회/NNG 동...  
3  [대구/NNP 경북/NNP 첨단/NNG 의료/NNP 산업/NNP 진흥/NNP 재단/...  
4  [국내/NNG 유통/NNG 탄산/NNP 음료/NNP 중/NNB 식품/NNG 의약품/...  
5  [북한/NNP 베트남/NNP 하노이/NNP 열리/VV 차/NNB 북미/NNP 정상회...  
6  [내년/NNG 1월/NNP 당진시/NNP 삽교호/NNP 수질/NNP 오염/NNP 총...  
7  [지방/NNG 선거/NNG 허위/NNP 사실/NNG 유포/NNG 혐의/NNG 기소/...  
8  [전국/NNP 요양/NNP 서비스/NNP 노동조합/NNP 경기/NNG 지부/NNG ...  
9  [옥천군/NNP 다람쥐/NNP 택시/NNP 이용/NNG 모습/NNG , 사진/NNP...

In [65]:
def ext_keysentences(sents, texts):
    
    summarizer = KeysentenceSummarizer(
    tokenize = komoran_tokenize,
    min_sim = 0.5,
    verbose = True
    )
    keysents = summarizer.summarize(texts) #### texts 넣은 결과랑 sents 넣은 결과 차이점...?
    
    for idx, rank, komoran_sent in keysents:
        print('#{} ({:.3}) : {}'.format(idx, rank, texts[idx]), end='\n\n')

In [66]:
ext_keysentences(dt['token_str'][0],dt['article_original'][0])

calculating textrank sentence similarity was done with 9 sents
trained TextRank. n sentences = 9
#1 (1.49) : 당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.

#0 (1.34) : 당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.

#8 (1.06) : 김기재 의장은 “본회의 의결과 제적의원 1/3의 발의가 있으면 행정사무조사특별위원회를 구성할 수 있다”며 “다음 달 초 위원들과 상의해 위원회를 구성한다면 당진시립합창단 관련 사안을 비롯해 사회복지기관 위수탁 등에 대해 다룰 계획”이라고 말했다.

#4 (0.981) : 권경선 문화관광과장은 “누가, 어떻게 해서 해당 문자가 나온 것인지 정확히 조사해봐야 알 수 있다”며 “전달받은 문자 내용도 최 의원이 언급한 부분만 있어, 중간 내용만을 가지고는 전체를 유추할 수 없다”고 전했다.

#6 (0.924) : 그동안 행정사무감사가 진행되고 있어 사태를 지켜봤다던 감사법무담당관실에서는 “관계된 사람들을 조사해 사태를 파악해야 하는데, 아직 조사에 대한 뚜렷한 계획이 없다”고 답했다.

#7 (0.912) : 한편 행감이 끝난 지난 12일 당진시의회에서는 당진시립합창단 문제를 비롯해 구체적인 조사가 필요한 부분에 대해 행정사무조사특별위원회를 구성해 운영하겠다고 밝혔다.

#3 (0.828) : 문제의 문자메세지를 전달받은 문화관광과는 감사법무담당관에게 조사를 의뢰했다.

#2 (0.737) : 이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며

In [64]:
data['ex_sent'][0]

['당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.',
 '당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.',
 '이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며 “공연 자체를 무력화해 당진시를 망신 주려는 행위”라며 해당 문자를 보낸 단원 등 연루된 사람들을 찾아 사실관계를 확인하고 징계 등 책임을 물어야 한다고 지적했다.']

In [68]:
data['token_pos'] = 'a'
for i in range(len(data)):
    data['token_pos'][i] = []
    for j in range(len(data['article_original'][i])):
        data['token_pos'][i].append(komoran_tokenize(data['article_original'][i][j]))

<ipython-input-68-0589b32d2615>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['token_pos'] = 'a'
/Users/ojoo/opt/anaconda3/envs/venv/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3417: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  exec(code_obj, self.user_global_ns, self.user_ns)


In [69]:
data['token_str'] = data['token_pos'].map(pos_to_string)
data['token_str'][0]

['당진시/NNP 문화/NNG 관광/NNP 과/NNG 대상/NNG 하/VV 행정사/NNP 감사/NNP 당진시/NNP 립/NNG 합창단/NNG 관계자/NNG 보내/VV 것/NNB 추정/NNG 문자/NNG 관련/NNG 당진시/NNP 의회/NNP 행정사/NNP 조사/NNG 특별/NNG 위원회/NNG 구성/NNG 조사/NNG 밝히/VV ',
 '당진시/NNP 의회/NNP 행정사/NNP 감사/NNP 일차/NNG 지나/VV 일/NNB 문화/NNG 관광/NNP 과/NNG 대상/NNG 하/VV 행/NNG 감/NNG 창/NNG 의원/NNG 당진시/NNP 립/NNG 합창단/NNG 정기/NNP 연주회/NNP 앞두/VV 문자/NNG 메세지/NNG 제보/NNG 받/VV 음향/NNG 팀/NNG 보내/VV 것/NNB 추정/NNG 해당/NNG 문자/NNG 합창단/NNG 소리/NNG 작/VA 내/VV 것/NNB 알/VV 있/VV 내용/NNG 말/NNG ',
 '공연/NNP 소리/NNG 작/VA 내/VV 것/NNB 합창단/NNG 임무/NNG 하/VV 것/NNB 공연/NNP 자체/NNG 무력/NNG 화해/NNP 당진시/NNP 망신/NNG 행위/NNG 해당/NNG 문자/NNG 보내/VV 단원/NNG 등/NNB 연루/NNG 사람/NNG 찾/VV 사실관계/NNP 확인/NNG 징계/NNG 등/NNB 책임/NNG 묻/VV 하/VV 지적/NNG ',
 '문제/NNG 문자/NNG 메세지/NNG 전달/NNG 받/VV 문화/NNG 관광/NNP 감사/NNP 법무/NNP 담당관/NNG 조사/NNG 의뢰/NNG ',
 '권/NNB 경선/NNP 문화/NNG 관광/NNP 과장/NNG 누가/NNP 어떻/VA 하/VV 해당/NNG 문자/NNG 나오/VV 것/NNB 조사/NNG 알/VV 수/NNB 있다/NNP 전달/NNG 받/VV 문자/NNP 내용/NNG 최/NNP 의원/NNG 언급/NNG 부분/NNG 있/VV 중간/NNG 내용/NNG 가지/VV 전체/NNG 유추/NNG 수/NNB 없/VA 전하/VV ',
 '감사/NNP 

In [70]:
data.head()

media         id                                   article_original  \
0  당진시대  327827480  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  국제신문  339840364  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  기호일보  371071597  [인천 부영공원 운영 생활야구협회 80여 동호회 팀에 260만 원씩 받아, 국유지로...   
3  대구일보  354806783  [대구·경북첨단의료산업진흥재단 의약생산센터는 항암주사제 무균충전 시설을 갖추고 있다...   
4  대구신문  347022773  [국내 유통되는 탄산음료 중 식품의약품안전처에 품질인증을 받은 제품이 하나도 없는 ...   

                                             ex_sent  \
0  [당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것...   
1  [미국 메이저리그(MLB)에서 활동하는 한국 선수들의 시즌 초반 희비가 엇갈리고 있...   
2  [16일 부평구와 협회 등에 따르면 부영공원 안에 있는 야구장을 구생활체육야구협회가...   
3  [대구·경북첨단의료산업진흥재단(이하 대구첨복재단) 의약생산센터는 주세제 특수제제인 ...   
4  [식품의약품안전처는 29일 여름철 어린이가 즐겨 마시는 탄산음료 282개와 혼합음료...   

                                           token_pos  \
0  [[당진시/NNP, 문화/NNG, 관광/NNP, 과/NNG, 대상/NNG, 하/VV...   
1  [[미국/NNP, 메이저/NNP, 리그/NNP, 활동/NNG, 한국/NNP, 선수/...   
2  [[인천/NNP, 부영공원/NNP, 운영/NNG, 생활/NNG, 야구/NNP, 협회...   
3  [[대구/NNP, 경북/NNP, 첨단/NNG, 의료/NNP, 산업/NNP, 진흥/N...   
4  [[국내/NNG, 유통/NNG, 탄산/NNP, 음료/NNP, 중/NNB, 식품/NN...   

                                           token_str  
0  [당진시/NNP 문화/NNG 관광/NNP 과/NNG 대상/NNG 하/VV 행정사/N...  
1  [미국/NNP 메이저/NNP 리그/NNP 활동/NNG 한국/NNP 선수/NNG 시즌...  
2  [인천/NNP 부영공원/NNP 운영/NNG 생활/NNG 야구/NNP 협회/NNG 동...  
3  [대구/NNP 경북/NNP 첨단/NNG 의료/NNP 산업/NNP 진흥/NNP 재단/...  
4  [국내/NNG 유통/NNG 탄산/NNP 음료/NNP 중/NNB 식품/NNG 의약품/...

In [35]:
# 토큰 + 품사

def token_pos(list_):
    keywords = keyword_extractor.summarize(list_, topk=30)
    token_pos = ''
    for word, rank in keywords:
        token_pos = token_pos + str(word) + ' '
    return token_pos

    

In [37]:
dt['token_pos'] = dt['article_original'].map(token_pos)
dt['token_pos'][0]

<ipython-input-37-66fba9ccd7f7>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dt['token_pos'] = dt['article_original'].map(token_pos)


'당진시/NNP 조사/NNG 합창단/NNG 것/NNB 문자/NNG 행정사/NNP 하/VV 감사/NNP 있/VV 립/NNG 관광/NNP 문화/NNG 위원회/NNG 구성/NNG 의회/NNP 보내/VV 내용/NNG 해당/NNG 받/VV 특별/NNG 추정/NNG 대상/NNG 과/NNG 수/NNB 대하/VV 등/NNB 지나/VV 일/NNB 행/NNG 감/NNG '

In [38]:
keywords = keyword_extractor.summarize(dt['article_original'][0], topk=30)
keywords

[('당진시/NNP', 2.9254544434376064),
 ('조사/NNG', 2.3702520395942197),
 ('합창단/NNG', 1.9674191790810989),
 ('것/NNB', 1.9514815677770292),
 ('문자/NNG', 1.8650788011945756),
 ('행정사/NNP', 1.8318490366187454),
 ('하/VV', 1.745465404264054),
 ('감사/NNP', 1.5336530447472225),
 ('있/VV', 1.4904499054399123),
 ('립/NNG', 1.3293924560105976),
 ('관광/NNP', 1.2268419128248897),
 ('문화/NNG', 1.2268419128248897),
 ('위원회/NNG', 1.1471082010564975),
 ('구성/NNG', 1.1471082010564975),
 ('의회/NNP', 1.0967826087016388),
 ('보내/VV', 1.0765615446840275),
 ('내용/NNG', 1.0332850837544818),
 ('해당/NNG', 1.0196729799450772),
 ('받/VV', 0.9328805926958859),
 ('특별/NNG', 0.9143598621341028),
 ('추정/NNG', 0.8534767220603268),
 ('대상/NNG', 0.8534767220603268),
 ('과/NNG', 0.8534767220603268),
 ('수/NNB', 0.8503183357819428),
 ('대하/VV', 0.8284958879168277),
 ('등/NNB', 0.8229920154536701),
 ('지나/VV', 0.8032838204294519),
 ('일/NNB', 0.8032838204294519),
 ('행/NNG', 0.8032838204294519),
 ('감/NNG', 0.8032838204294519)]

In [105]:
summarizer = KeysentenceSummarizer(
    tokenize = komoran_tokenize,
    min_sim = 0.5,
    verbose = True
    )

In [106]:
# sents 넣은 ver
def ext_keysentences_sents(sents, texts):
    
    ext_keysent = ''
    
    keysents = summarizer.summarize(sents) 
    
    for idx, rank, komoran_sent in keysents:
        ext_keysent = ext_keysent + str(texts[idx]) + '\n'
    
    return ext_keysent

In [107]:
# texts 넣은 ver
def ext_keysentences_texts(sents, texts):
    
    keysents = summarizer.summarize(texts) 
    
    ext_keysent = ''
    
    for idx, rank, komoran_sent in keysents:
        ext_keysent = ext_keysent + str(texts[idx]) + '\n'
    
    return ext_keysent

In [111]:
data['ext_keysent_sent']=''
data['ext_keysent_text']=''

for i in range(len(data)):
    data['ext_keysent_sent'][i] = ext_keysentences_sents(data['token_str'][i],data['article_original'][i])
    data['ext_keysent_text'][i] = ext_keysentences_texts(data['token_str'][i],data['article_original'][i])

calculating textrank sentence similarity was done with 9 sents
trained TextRank. n sentences = 9
calculating textrank sentence similarity was done with 9 sents
trained TextRank. n sentences = 9
calculating textrank sentence similarity was done with 21 sents
trained TextRank. n sentences = 21
calculating textrank sentence similarity was done with 21 sents
trained TextRank. n sentences = 21
calculating textrank sentence similarity was done with 19 sents
trained TextRank. n sentences = 19
calculating textrank sentence similarity was done with 19 sents
trained TextRank. n sentences = 19
calculating textrank sentence similarity was done with 10 sents
trained TextRank. n sentences = 10
calculating textrank sentence similarity was done with 10 sents
trained TextRank. n sentences = 10
calculating textrank sentence similarity was done with 13 sents
trained TextRank. n sentences = 13
calculating textrank sentence similarity was done with 13 sents
trained TextRank. n sentences = 13
calculating te

In [114]:
data['ext_keysent_sent'][0]

'당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.\n당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.\n김기재 의장은 “본회의 의결과 제적의원 1/3의 발의가 있으면 행정사무조사특별위원회를 구성할 수 있다”며 “다음 달 초 위원들과 상의해 위원회를 구성한다면 당진시립합창단 관련 사안을 비롯해 사회복지기관 위수탁 등에 대해 다룰 계획”이라고 말했다.\n권경선 문화관광과장은 “누가, 어떻게 해서 해당 문자가 나온 것인지 정확히 조사해봐야 알 수 있다”며 “전달받은 문자 내용도 최 의원이 언급한 부분만 있어, 중간 내용만을 가지고는 전체를 유추할 수 없다”고 전했다.\n그동안 행정사무감사가 진행되고 있어 사태를 지켜봤다던 감사법무담당관실에서는 “관계된 사람들을 조사해 사태를 파악해야 하는데, 아직 조사에 대한 뚜렷한 계획이 없다”고 답했다.\n한편 행감이 끝난 지난 12일 당진시의회에서는 당진시립합창단 문제를 비롯해 구체적인 조사가 필요한 부분에 대해 행정사무조사특별위원회를 구성해 운영하겠다고 밝혔다.\n문제의 문자메세지를 전달받은 문화관광과는 감사법무담당관에게 조사를 의뢰했다.\n하지만 감사법무담당관실에서 아직 조사가 이뤄지지 않고 있어 당진시가 사태의 심각성을 인지하지 못하고 있다는 지적이다.\n이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며 “공연 자체를 무력화해 당진시를 망신 주려는 행위”라며 해당 문자를 보낸 단원 등 연루된 사람들을 찾아 사실관계를 확인하고 징계 등 책임을 물어야 한다고 지적했다.\n'

In [115]:
data.to_csv('TextRank.csv', encoding='utf-8-sig')

In [116]:
for i in range(len(data)):
    data['ext_keysent_sent'][i] = str(data['ext_keysent_sent'][i]).split('\n')[:3]
    data['ext_keysent_text'][i] = str(data['ext_keysent_text'][i]).split('\n')[:3]

In [117]:
data['ext_keysent_sent'][0]

['당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.',
 '당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.',
 '김기재 의장은 “본회의 의결과 제적의원 1/3의 발의가 있으면 행정사무조사특별위원회를 구성할 수 있다”며 “다음 달 초 위원들과 상의해 위원회를 구성한다면 당진시립합창단 관련 사안을 비롯해 사회복지기관 위수탁 등에 대해 다룰 계획”이라고 말했다.']

#### 성능 올릴 때 해볼만한 것

- **window 크기**
  </br> window 를 -1 로 설정하면 한 문장에서 얼마나 떨어져 있던지 상관없이 cooccurrence 를 계산하며, window 가 1 보다 클 경우에는 해당 간격만큼만 떨어진 단어들 간에만 cooccurrence 를 인정
  </br> window 의 크기를 바꾼다 하여도 큰 변화는 없습니다. 약간의 순위 변동은 있지만, 큰 맥락이 변하지는 않습니다.
  
- **토크나이저**
- **bias 설정**
  </br> 뉴스 기사의 경우 첫 문장이나 마지막 문장이 중요한 경우가 많으므로 가중치를 두는 방법을 생각해볼 수 있음!

In [119]:
data['ex_sent'][0]

['당진시 문화관광과를 대상으로 하는 행정사무감사에서 당진시립합창단 관계자가 보낸 것으로 추정되는 문자와 관련해 당진시의회가 행정사무조사특별위원회를 구성해 조사하겠다고 밝혔다.',
 '당진시의회 행정사무감사 3일차였던 지난 6일 문화관광과를 대상으로 하는 행감에서 최창용 의원은 “(당진시립합창단 정기연주회를 앞두고) 문자메세지를 제보받았다”며 “(음향팀에 보낸 것으로 추정되는) 해당 문자에는 ‘합창단이 소리를 작게 낼 것이니 알고 있으라’는 내용이었다”고 말했다.',
 '이어 “공연에서 소리를 작게 낸다는 것은 합창단으로서 그 임무를 하지 않겠다는 것”이며 “공연 자체를 무력화해 당진시를 망신 주려는 행위”라며 해당 문자를 보낸 단원 등 연루된 사람들을 찾아 사실관계를 확인하고 징계 등 책임을 물어야 한다고 지적했다.']